## Import de bibliotecas

In [1]:
import sys
sys.path.append('..\..')

In [5]:
import pandas as pd
import numpy as np
from config import *
import matplotlib.pyplot as plt
import plotly.express as px
import plotly.graph_objects as go
import statistics as stat
pd.set_option('display.max_columns', 500)
from functools import reduce

from sklearn import datasets, linear_model
from sklearn.metrics import mean_squared_error, r2_score, confusion_matrix
from sklearn.linear_model import LogisticRegression
from sklearn import svm
from sklearn.preprocessing import StandardScaler
from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import train_test_split 

In [6]:
df = pd.read_csv(path_arquivo_treino)
df = df.drop(df[df.vh_weight < 50].index)
df.shape

FileNotFoundError: [Errno 2] File D:\Users\vicml\Documents\Projetos\pricing-game\A\dados\entrada\training.csv does not exist: 'D:\\Users\\vicml\\Documents\\Projetos\\pricing-game\\A\\dados\\entrada\\training.csv'

### Feature engineering

In [ ]:
df_ano_1 = df[df['year']==1]
df_ano_1 = df_ano_1.rename(columns={'claim_amount':'claim_amount_1','pol_no_claims_discount':'pol_no_claims_discount_1'})
#df_ano_1['claim_amount_1'] = (df_ano_1['claim_amount_1']>0).astype(int)

df_ano_2 = df[df['year']==2]
df_ano_2 = df_ano_2.rename(columns={'claim_amount':'claim_amount_2','pol_no_claims_discount':'pol_no_claims_discount_2'})
#df_ano_2['claim_amount_2'] = (df_ano_2['claim_amount_2']>0).astype(int)

df_ano_3 = df[df['year']==3]
df_ano_3 = df_ano_3.rename(columns={'claim_amount':'claim_amount_3','pol_no_claims_discount':'pol_no_claims_discount_3'})
#df_ano_3['claim_amount_3'] = (df_ano_3['claim_amount_3']>0).astype(int)

df_ano_4 = df[df['year']==4]
df_ano_4 = df_ano_4.rename(columns={'claim_amount':'claim_amount_4'})
df_ano_4['claim_amount_4'] = (df_ano_4['claim_amount_4']>0).astype(int)

dfs = [ df_ano_1[['id_policy','claim_amount_1','pol_no_claims_discount_1']]
       ,df_ano_2[['id_policy','claim_amount_2','pol_no_claims_discount_2']]
       ,df_ano_3[['id_policy','claim_amount_3','pol_no_claims_discount_3']]
       ,df_ano_4[['id_policy','claim_amount_4']]]

In [ ]:
colunas = list(df_ano_1.columns)
df_merged = reduce(lambda  left,right: pd.merge(left,right,on=['id_policy'],
                                            how='inner'), dfs)

dfs = [df_ano_1[['id_policy', 'year', 'pol_coverage',
       'pol_duration', 'pol_sit_duration', 'pol_pay_freq', 'pol_payd',
       'pol_usage', 'drv_sex1', 'drv_age1', 'drv_age_lic1', 'drv_drv2',
       'drv_sex2', 'drv_age2', 'drv_age_lic2', 'vh_make_model', 'vh_age',
       'vh_fuel', 'vh_type', 'vh_speed', 'vh_value', 'vh_weight', 'population',
       'town_surface_area']],df_merged]
df_merged = reduce(lambda  left,right: pd.merge(left,right,on=['id_policy'],
                                            how='inner'), dfs)

In [ ]:
filtro =  df['vh_make_model'].value_counts()
modelos = filtro[filtro>=200]
df_modelos = df[df['vh_make_model'].isin(modelos.index)]

contagem_veiculos = df_modelos.groupby('vh_make_model')['id_policy'].count()
contagem_claim_veiculos = df_modelos[ df['claim_amount'] > 0 ].groupby('vh_make_model')['id_policy'].count()

prob_claim_veiculos = (contagem_claim_veiculos / contagem_veiculos).fillna(0)
carros_maior_prob = list(prob_claim_veiculos[prob_claim_veiculos>0.15].index)
carros_menor_prob = list(prob_claim_veiculos[prob_claim_veiculos<0.05].index)

In [ ]:

df_merged['pol_coverage_2'] = df_merged['pol_coverage'].map({'Min':1,'Med1':2,'Med2':3,'Max':4})
df_merged['pol_pay_freq_2'] = df_merged['pol_pay_freq'].map({'Yearly':1,'Biannual':2,'Quarterly':4,'Monthly':12})
df_merged['pol_payd_2'] = (df_merged['pol_payd']=='Yes').astype(int)
df_merged = pd.concat([df_merged,pd.get_dummies(df_merged['pol_usage'], drop_first = True, prefix = 'pol_usage')], axis=1)
df_merged['drv_sex1_2'] = (df_merged['drv_sex1']=='F').astype(int)
df_merged['drv_drv2_2'] = (df_merged['drv_drv2']=='Yes').astype(int)
df_merged['grupo_risco_1'] = ((df_merged['pol_usage']=='Professional')&(df_merged['pol_coverage']=='Max')).astype(int)
df_merged['grupo_risco_2'] = ((df_merged['pol_usage']=='WorkPrivate')&(df_merged['pol_coverage']=='Min')).astype(int)
df_merged['grupo_risco_3'] = df_merged['vh_make_model'].isin(carros_maior_prob).astype(int)
df_merged['grupo_risco_4'] = df_merged['vh_make_model'].isin(carros_menor_prob).astype(int)
df_merged['grupo_risco_5'] = ((df_merged['vh_age']>15) ).astype(int)
df_merged['grupo_risco_6'] = ((df_merged['vh_age']>0) &(df_merged['vh_age']<6)).astype(int)
df_merged['weight_p_speed'] = df_merged['vh_weight']/df_merged['vh_speed']
df_merged['vh_value_risk'] = df_merged['vh_value']/df_merged['pol_coverage_2']

df_merged['vh_type_2'] = (df_merged['vh_type']=='Commercial').astype(int)

df_fuel = pd.get_dummies(df_merged['vh_fuel'], drop_first = True, prefix = 'fuel')
df_merged = pd.concat([df_merged,df_fuel], axis=1)

contagem_carros = df['vh_make_model'].value_counts()
lista_50_carros = contagem_carros[contagem_carros>1000].index
df_merged['vh_make_model_2'] = df_merged['vh_make_model'].copy()
df_merged.loc[df_merged['vh_make_model'].isin(lista_50_carros)==False, 'vh_make_model_2']='Outros'
df_modelos = pd.get_dummies(df_merged['vh_make_model_2'], drop_first = True, prefix = 'model')
df_merged = pd.concat([df_merged,df_modelos], axis=1)

### Modelo para prever 0 claim

In [4]:
features = ['claim_amount_1','pol_no_claims_discount_1',
            'claim_amount_2','pol_no_claims_discount_2',
            'claim_amount_3','pol_no_claims_discount_3',
            'pol_coverage_2','drv_age_lic1', 'vh_weight',
            'fuel_Gasoline','drv_age1','vh_speed','vh_age',
            'vh_value','population','grupo_risco_2',
            'grupo_risco_5','grupo_risco_6','vh_value_risk']

df_merged = df_merged.rename(columns= {'claim_amount_4':'y'})

NameError: name 'df_merged' is not defined

In [9]:
df_sample = df_merged.sample(20000)
X = df_sample[features].copy()
y = df_sample['y']

In [10]:
X.fillna(0,inplace = True)

#### Baseline

In [11]:
df_sample['previsao_baseline'] = ((df_sample['claim_amount_1'] +
                                   df_sample['claim_amount_2'] + 
                                   df_sample['claim_amount_3'])>0).astype(int)
confusion_matrix(y,df_sample['previsao_baseline'])

array([[13401,  4754],
       [ 1105,   740]], dtype=int64)

#### Regressão Logistica

In [28]:
w = {0:1,1:9}
clf_rl = LogisticRegression(max_iter = 1000, class_weight=w).fit(X, y)

In [29]:
clf_rl.score(X, y)

0.58415

In [30]:
len(df[(df['claim_amount']==0) & (df['year']==4)])/len(df[df['year']==4])

0.9071293352202761

In [31]:
y_pred = clf_rl.predict(X) 
confusion_matrix(y,y_pred)

array([[10582,  7573],
       [  744,  1101]], dtype=int64)

In [16]:
clf_rl.coef_

array([[ 6.21405837e-05,  2.59453317e-04,  1.96063385e-04,
         2.91637364e-04,  1.15100671e-04,  2.88397763e-04,
         1.19406059e-03,  3.57038282e-03,  3.14101525e-04,
        -2.53017312e-03, -8.84409110e-03,  5.00342894e-04,
        -3.79147211e-02,  2.47488121e-05, -1.58854821e-06,
        -2.07299163e-04, -1.49979565e-03,  1.62927401e-03,
        -9.24210384e-05]])

#### PCA

In [17]:
from sklearn.decomposition import PCA,KernelPCA

In [18]:
pca = KernelPCA(n_components=3)
X_pca = pca.fit_transform(X)
df_pca = pd.DataFrame(X_pca,columns = ['x1','x2','x3'])
df_pca['y'] = y.values
df_pca['y'] = df_pca['y'].astype(str)

In [23]:
df_pca['y'].value_counts()

0    18155
1     1845
Name: y, dtype: int64

In [22]:
df_pca[
    (df_pca['x1']>-5e3) &
    (df_pca['x1']<15e3) &
    (df_pca['x2']<0)
]['y'].value_counts()

0    8221
1    1056
Name: y, dtype: int64

In [20]:
px.scatter(df_pca,x='x1',y='x2',color = 'y')

In [21]:
px.scatter_3d(df_pca,x='x1',y='x2',z='x3',color = 'y')

In [56]:
pca.components_

array([[ 2.05811575e-03, -3.59691310e-07,  1.43747961e-03,
        -2.90305105e-07,  7.22505990e-04, -2.27130774e-07,
         8.47335104e-07, -3.36315341e-05,  2.04949286e-02,
        -1.13232611e-05, -8.17978690e-05,  1.43977003e-03,
        -4.09555856e-05,  9.40342138e-01, -4.29016459e-04,
         7.00069427e-07, -2.59642138e-06,  3.41714251e-07,
         3.39599074e-01],
       [-1.06254767e-02,  2.25244858e-06, -7.81132871e-03,
         1.74345448e-06, -9.22494628e-03,  1.38634980e-06,
        -2.01519685e-04, -1.40836875e-04, -8.46777492e-03,
         1.16062444e-05, -9.30026674e-05, -1.36433192e-03,
         7.00741567e-04, -3.39408647e-01, -6.29567703e-03,
         4.40910037e-05,  2.91691349e-05, -3.23072848e-05,
         9.40440848e-01]])

#### Support Vector

In [21]:
w={0:1,1:1.5}

In [29]:
clf_sv = svm.SVC(kernel='linear',class_weight=w,gamma =2, tol=2)

In [30]:
scaler = StandardScaler()
scaler.fit(X)

StandardScaler()

In [31]:
clf_sv.fit(scaler.transform(X), y)

SVC(class_weight={0: 1, 1: 1.5}, gamma=2, kernel='linear', tol=2)

In [32]:
clf_sv.score(X,y)

0.9076

In [33]:
arr = clf_sv.decision_function(X)

In [34]:
arr[15]

-986.3936098954186

In [35]:
y_pred = clf_sv.predict(X) 
confusion_matrix(y,y_pred)

array([[4538,    6],
       [ 456,    0]], dtype=int64)

#### Random Forest

In [23]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.33,random_state=0)
w = {0:1,1:6}

In [24]:
clf_rf = RandomForestClassifier(n_estimators=1000,max_depth=5,verbose=1,class_weight=w)

In [25]:
clf_rf.fit(X_train,y_train)

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done 1000 out of 1000 | elapsed:   13.0s finished


RandomForestClassifier(class_weight={0: 1, 1: 6}, max_depth=5,
                       n_estimators=1000, verbose=1)

In [26]:
clf_rf.score(X_test,y_test)

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done 1000 out of 1000 | elapsed:    0.9s finished


0.8910609857978279

In [27]:
clf_rf.score(X_train,y_train)

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done 1000 out of 1000 | elapsed:    1.8s finished


0.8935096285729961

In [28]:
y_pred = clf_rf.predict(X_test) 
confusion_matrix(y_test,y_pred)

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done 1000 out of 1000 | elapsed:    1.0s finished


array([[15892,   402],
       [ 1554,   107]], dtype=int64)

In [29]:
y_pred = clf_rf.predict(X_train) 
confusion_matrix(y_train,y_pred)

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done 1000 out of 1000 | elapsed:    1.9s finished


array([[32292,   770],
       [ 3112,   280]], dtype=int64)

In [30]:
clf_rf.feature_importances_

array([0.03667932, 0.01290989, 0.0426247 , 0.01564396, 0.02446721,
       0.02086047, 0.16142905, 0.02199753, 0.03764242, 0.05671457,
       0.02041259, 0.02139862, 0.239209  , 0.05497749, 0.01615662,
       0.04120004, 0.0797497 , 0.05255646, 0.04337034])

In [31]:
list(zip(X.columns,clf_rf.feature_importances_))

[('claim_amount_1', 0.03667931983456445),
 ('pol_no_claims_discount_1', 0.012909891663776304),
 ('claim_amount_2', 0.04262470230850816),
 ('pol_no_claims_discount_2', 0.015643963643373837),
 ('claim_amount_3', 0.024467214594953247),
 ('pol_no_claims_discount_3', 0.020860469033432735),
 ('pol_coverage_2', 0.16142904754609327),
 ('drv_age_lic1', 0.021997529646379712),
 ('vh_weight', 0.03764242278187647),
 ('fuel_Gasoline', 0.05671457183662164),
 ('drv_age1', 0.020412594843155895),
 ('vh_speed', 0.02139862238669616),
 ('vh_age', 0.23920900470976583),
 ('vh_value', 0.054977486853982564),
 ('population', 0.016156620907305),
 ('grupo_risco_2', 0.04120004004847057),
 ('grupo_risco_5', 0.07974969684584363),
 ('grupo_risco_6', 0.05255646312538122),
 ('vh_value_risk', 0.04337033738981928)]